In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=2, stride=2, padding=0),  
            nn.ELU(),
            nn.Conv2d(32, 32, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(32, 64, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(64, 128, kernel_size=2, stride=2, padding=0),
            nn.ELU(), 
            nn.Conv2d(128, 256, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Conv2d(256, 512, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        features_dim = 512
        self.encoder = VisualEncoder()
        self.encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AngelaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.action_head = nn.Linear(features_dim, action_space.n)
        self.value_head = nn.Linear(features_dim, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.encoder.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs'].permute(0, 3, 1, 2).float() / 255.0
        if self.use_cuda:
            obs.cuda()
            
        features = self.encoder(obs)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C8']))
    env = PovOnlyWrapper(env)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [ ]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name": "PPO C8 pretrained (AngelaCNN) (3 noops after placement)"
                  }
              }

        },
        loggers=[WandbLogger])

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)
2021-10-08 22:23:55,233	INFO wandb.py:170 -- Already logged into W&B.
2021-10-08 22:23:55,254	ERROR syncer.py:72 -- Log sync requires rsync to be installed.


wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id c4eb6_00000 but id 6c5b8_00000 is set.
wandb: wandb version 0.12.4 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=40112) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=40112)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=40112) 2021-10-08 22:23:58,754	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=40112) 2021-10-08 22:23:58,754	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=40111) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=40111)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=40112) 2021-10-08 22:24:04,523	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=40111) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=40111)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=40111) /root/miniconda/envs/py37/lib/python3.7/

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-10-08_22-25-09
  done: false
  episode_len_mean: 413.0
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: -7.0
  episode_reward_min: -14.0
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.680601273642646
          entropy_coeff: 0.009999999999999998
          kl: 0.01061723793506031
          policy_loss: 0.014398261490795348
          total_loss: 0.3600214495841
          vf_explained_var: -0.008035365492105484
          vf_loss: 0.3703057582800587
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_since_restore: 1
  node_ip: 192.168.3.5
  nu

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-10-08_22-25-30
  done: false
  episode_len_mean: 403.5
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: -3.5
  episode_reward_min: -14.0
  episodes_this_iter: 2
  episodes_total: 4
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.7041153642866345
          entropy_coeff: 0.009999999999999998
          kl: 0.011423616325345927
          policy_loss: 0.014449085998866294
          total_loss: 0.007905774811903635
          vf_explained_var: 0.19078736007213593
          vf_loss: 0.018213119099123612
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  iterations_since_restore: 2
  node_ip: 192.168.3

...

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2267000
  custom_metrics: {}
  date: 2021-10-09_14-09-22
  done: false
  episode_len_mean: 366.41
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: 0.0
  episode_reward_min: 0.0
  episodes_this_iter: 3
  episodes_total: 6330
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 1.40601251232656
          cur_lr: 5.000000000000001e-05
          entropy: 1.5271601412031386
          entropy_coeff: 0.009999999999999998
          kl: 0.00994839814612855
          policy_loss: -0.016706375032663347
          total_loss: -0.017970605856842466
          vf_explained_var: -0.30679625272750854
          vf_loss: 1.9799254808579765e-05
    num_agent_steps_sampled: 2267000
    num_agent_steps_trained: 2267000
    num_steps_sampled: 2267000
    num_steps_trained: 2267000
  iterations_since_restore: 2267


Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2268000
  custom_metrics: {}
  date: 2021-10-09_14-09-49
  done: false
  episode_len_mean: 364.23
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: 0.0
  episode_reward_min: 0.0
  episodes_this_iter: 4
  episodes_total: 6334
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 1.40601251232656
          cur_lr: 5.000000000000001e-05
          entropy: 1.6974533107545642
          entropy_coeff: 0.009999999999999998
          kl: 0.0073814462807389935
          policy_loss: -0.06324908547103406
          total_loss: -0.06981407509495814
          vf_explained_var: 0.0010850760154426098
          vf_loss: 3.1138829935015466e-05
    num_agent_steps_sampled: 2268000
    num_agent_steps_trained: 2268000
    num_steps_sampled: 2268000
    num_steps_trained: 2268000
  iterations_since_restore: 2268

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2269000
  custom_metrics: {}
  date: 2021-10-09_14-10-11
  done: false
  episode_len_mean: 362.8
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: 0.0
  episode_reward_min: 0.0
  episodes_this_iter: 2
  episodes_total: 6336
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 1.40601251232656
          cur_lr: 5.000000000000001e-05
          entropy: 1.8225307226181031
          entropy_coeff: 0.009999999999999998
          kl: 0.009138194326383124
          policy_loss: -0.08174182960970534
          total_loss: -0.08709399743626516
          vf_explained_var: -0.4979848563671112
          vf_loss: 2.4723173954852327e-05
    num_agent_steps_sampled: 2269000
    num_agent_steps_trained: 2269000
    num_steps_sampled: 2269000
    num_steps_trained: 2269000
  iterations_since_restore: 2269
  n

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2270000
  custom_metrics: {}
  date: 2021-10-09_14-10-36
  done: false
  episode_len_mean: 363.17
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: 0.0
  episode_reward_min: 0.0
  episodes_this_iter: 3
  episodes_total: 6339
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 1.40601251232656
          cur_lr: 5.000000000000001e-05
          entropy: 1.8526235275798373
          entropy_coeff: 0.009999999999999998
          kl: 0.005698106654839129
          policy_loss: -0.05359576565937863
          total_loss: -0.06396399262464708
          vf_explained_var: -0.5291381478309631
          vf_loss: 0.00014639611999882617
    num_agent_steps_sampled: 2270000
    num_agent_steps_trained: 2270000
    num_steps_sampled: 2270000
    num_steps_trained: 2270000
  iterations_since_restore: 2270
  

Result for PPO_my_env_6c5b8_00000:
  agent_timesteps_total: 2271000
  custom_metrics: {}
  date: 2021-10-09_14-11-00
  done: false
  episode_len_mean: 363.06
  episode_media: {}
  episode_reward_max: 0.0
  episode_reward_mean: 0.0
  episode_reward_min: 0.0
  episodes_this_iter: 3
  episodes_total: 6342
  experiment_id: fec3e22c8569417c9ec22976fe85ed14
  hostname: linar-Z390-GAMING-X
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 1.40601251232656
          cur_lr: 5.000000000000001e-05
          entropy: 1.812007607354058
          entropy_coeff: 0.009999999999999998
          kl: 0.005179332406223638
          policy_loss: 0.08376175527357393
          total_loss: 0.07300720279001527
          vf_explained_var: -0.1040421724319458
          vf_loss: 8.331598502182815e-05
    num_agent_steps_sampled: 2271000
    num_agent_steps_trained: 2271000
    num_steps_sampled: 2271000
    num_steps_trained: 2271000
  iterations_since_restore: 2271
  node